## Modelo de predicción XGBoost.

#### Librerías

In [48]:
# Technique for oversampling imbalanced data
from imblearn.over_sampling import SMOTE  

# XGBoost classifier
from xgboost import XGBClassifier  

# Handling data and numerical operations
import pandas as pd  
import numpy as np  

# Scikit-learn functions for data splitting and model evaluation
from sklearn.model_selection import train_test_split  # Splits data into training and testing sets
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score, confusion_matrix, classification_report
# Metrics to evaluate model performance

# Additional metrics for evaluating model performance
from sklearn.metrics import precision_recall_curve, roc_auc_score 

#### Preprocesamiento de los datos. 

In [50]:
def process_sales_data(file_path):
    """
    This function processes sales data from a CSV file to prepare it for analysis.
    
    Args:
    file_path (str): Path to the CSV file containing the sales data.

    Returns:
    df_sinID (DataFrame): Processed DataFrame without the "customer_id" column.
    result_df (DataFrame): Fully processed DataFrame with the "customer_id" and all other columns.
    """
    # Read the CSV file
    df_sales = pd.read_csv(file_path)
    
    # Remove rows with null values in the "churn_next_month" column
    df_sales = df_sales.dropna(subset=["churn_next_month"])
    
    # Convert the "month" column to date format
    df_sales["month"] = pd.to_datetime(df_sales["month"].astype(str), format="%Y%m")
    
    # Sort values by "customer_id" and "month"
    df_sales = df_sales.sort_values(by=["customer_id", "month"])
    
    # Get customers who churn next month
    churn_customers = df_sales[df_sales["churn_next_month"] == 1]["customer_id"]
    
    # Group by "customer_id" and create a list of "amount"
    df_grouped = df_sales.groupby("customer_id")["amount"].apply(list).reset_index()
    
    # Get the maximum length of lists in the "amount" column
    max_length = df_grouped["amount"].apply(len).max()
    
    # Pad lists with zeros to have the same length
    df_grouped["amount"] = df_grouped["amount"].apply(
        lambda x: [0] * (max_length - len(x)) + x
    )
    
    # Create a DataFrame from the "amount" lists
    amount_df = pd.DataFrame(
        df_grouped["amount"].to_list(), columns=[f"amount_{i+1}" for i in range(max_length)]
    )
    
    # Concatenate the original DataFrame with the "amount" DataFrame
    result_df = pd.concat([df_grouped.drop(columns=["amount"]), amount_df], axis=1)
    
    # Add the "churn_next_month" column
    result_df["churn_next_month"] = 0
    result_df.loc[result_df["customer_id"].isin(churn_customers), "churn_next_month"] = 1
    
    # Remove the "customer_id" column
    df_sinID = result_df.iloc[:, 1:-1]
    
    return df_sinID, result_df

# Process sales data from the given CSV file
df_sinID, result_df = process_sales_data("sales.csv")

#### Visualización de datos preprocesados

In [24]:
# Displaying the df_sinID dataset
df_sinID

amount_1  amount_2  amount_3  amount_4  amount_5  amount_6  amount_7  \
0        49.0843   45.1530   28.5473   51.2210   70.6396   66.4318   59.0138   
1       131.2384  128.5816  112.9212  116.7928  122.2274  117.4014  121.4014   
2         0.0000    0.0000    0.0000    0.0000    0.0000    0.0000    0.0000   
3         0.0000    0.0000    0.0000    0.0000    0.0000    0.0000    0.0000   
4         0.0000    0.0000    0.0000    0.0000    0.0000    0.0000    0.0000   
...          ...       ...       ...       ...       ...       ...       ...   
169101    0.0000    0.0000    0.0000    0.0000    0.0000    0.0000    0.0000   
169102  192.6681  139.2060  150.4393  172.0419  172.9516  215.3614  292.2377   
169103    6.6572    3.8746    4.4804   15.2166   26.0712   39.0483   25.6564   
169104    0.0000    0.0000    0.0000    0.0000    0.0000    0.0000    0.0000   
169105  127.0988   96.2371   88.9208   76.5194  113.3400  111.3280  123.0147   

        amount_8   amount_9  amount_10  ...   amount_39  amount_40  \
0        90.7214   64.17770    37.6583  ...   26.735078    46.6362   
1       164.7714  183.11890   189.3811  ...   67.940100    66.5099   
2         0.0000    0.00000     0.0000  ...   19.302500    27.0764   
3         0.0000  276.91930   305.8946  ...  254.545378   236.8439   
4         0.0000    0.00000    33.4624  ...  195.240100   204.9193   
...          ...        ...        ...  ...         ...        ...   
169101    0.0000    0.00000     0.0000  ...  297.041300   284.6913   
169102  272.9573  213.35295   180.2159  ...  190.105137   228.8408   
169103   22.2324   16.00750     2.9235  ...   10.445800    26.4990   
169104    0.0000    0.00000     0.0000  ...    0.000000    38.3707   
169105  105.8403   97.38480    88.6620  ...   52.236700     0.0000   

         amount_41   amount_42  amount_43   amount_44   amount_45  amount_46  \
0        47.563753   18.175400   25.57240   40.299500   30.681900   32.89900   
1        84.713800   50.651800   51.80010   62.251200   62.557500   78.85200   
2        29.728700   36.703000   33.88510   38.992500   31.752600    9.95880   
3       230.684373  208.593832  171.01490  123.454700   96.027300  140.13660   
4       306.376800  231.761000  259.85190  297.605900  312.957300  272.97410   
...            ...         ...        ...         ...         ...        ...   
169101  258.322400  479.959300  580.58990  539.388298  580.148800  593.30555   
169102  296.405694  191.056700  217.19713  270.499378  169.834676   72.55850   
169103   28.462800   24.343000   28.24100   21.125300   30.871800   15.11440   
169104   52.765400   90.631500   59.78650   62.557600   41.176800   18.14050   
169105   32.124000    6.692500    6.41070    0.000000    0.000000    0.00000   

         amount_47  amount_48  
0         3.522400     8.1719  
1        58.700800    53.2764  
2         3.134900     3.5928  
3        14.331900     5.5300  
4       264.353893   199.5718  
...            ...        ...  
169101  456.716700   378.7065  
169102    2.493800     0.1656  
169103    2.198900    11.5473  
169104   14.758900     1.3385  
169105    0.000000     0.0000  

[169106 rows x 48 columns]

#### Calculando diferencias cada dos meses

In [51]:
def porcentaje_cambio(suma_anterior, suma_actual):
    """
    Calculate the percentage change between two sums.

    Args:
    suma_anterior (float): The previous sum.
    suma_actual (float): The current sum.

    Returns:
    float: The percentage change.
    """
    return (suma_actual - suma_anterior) / suma_anterior


def calcular_cambios(df_sinID, result_df):
    """
    Calculate percentage changes for each customer and add relevant identifiers.

    Args:
    df_sinID (DataFrame): Processed DataFrame without customer_id.
    result_df (DataFrame): Fully processed DataFrame with customer_id.

    Returns:
    DataFrame: DataFrame containing percentage changes and identifiers.
    """
    resultados = []

    # Iterate over each row in df_sinID
    for _, row in df_sinID.iterrows():
        array = row.values
        cambios = []

        # Calculate percentage change for each consecutive sum pair
        for i in range(len(array) - 2):
            suma_anterior = array[i] + array[i + 1]
            suma_actual = array[i + 1] + array[i + 2]
            cambio = porcentaje_cambio(suma_anterior, suma_actual)
            cambios.append(cambio)

        resultados.append(cambios)

    # Create a DataFrame from the list of changes
    resultados_df = pd.DataFrame(
        resultados, columns=[f"change_{i+1}" for i in range(len(resultados[0]))]
    )

    # Replace NaN and infinite values
    resultados_df.fillna(0, inplace=True)
    resultados_df.replace([np.inf, -np.inf], 1, inplace=True)

    # Add customer_id and churn_next_month columns
    resultados_df["customer_id"] = result_df["customer_id"]
    resultados_df["churn_next_month"] = result_df["churn_next_month"]

    return resultados_df

# Calculate changes for the given data
resultados_df = calcular_cambios(df_sinID, result_df)
resultados_df


C:\Users\abrah\AppData\Local\Temp\ipykernel_9760\3888782682.py:12: RuntimeWarning: invalid value encountered in scalar divide
  return (suma_actual - suma_anterior) / suma_anterior
C:\Users\abrah\AppData\Local\Temp\ipykernel_9760\3888782682.py:12: RuntimeWarning: divide by zero encountered in scalar divide
  return (suma_actual - suma_anterior) / suma_anterior


change_1  change_2  change_3  change_4  change_5  change_6  change_7  \
0      -0.217929  0.082333  0.527682  0.124821 -0.084816  0.193627  0.034487   
1      -0.070500 -0.048814  0.040512  0.002546 -0.003447  0.198365  0.215665   
2       0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
3       0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  1.000000   
4       0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
...          ...       ...       ...       ...       ...       ...       ...   
169101  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
169102 -0.127243  0.113366  0.069810  0.125566  0.307191  0.113467 -0.139571   
169103 -0.206688  1.357510  1.096147  0.577209 -0.006370 -0.259887 -0.201486   
169104  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
169105 -0.170944 -0.106491  0.147601  0.183339  0.043062 -0.023417 -0.111992   

        change_8  change_9  change_10  ...  change_39  change_40  change_41  \
0      -0.342566 -0.138510   0.533100  ...   0.283880  -0.302132  -0.334524   
1       0.070740 -0.063157  -0.073689  ...   0.124758  -0.104865  -0.243147   
2       0.000000  0.000000   0.000000  ...   0.224805   0.169467   0.062567   
3       1.104634 -0.054558  -0.065028  ...  -0.048558  -0.060424  -0.135835   
4       1.000000  3.523157   0.687503  ...   0.277731   0.052497  -0.086455   
...          ...       ...        ...  ...        ...        ...        ...   
169101  0.000000  0.000000   0.000000  ...  -0.066558   0.359601   0.436510   
169102 -0.190704  0.054399   0.108448  ...   0.253733  -0.071936  -0.162492   
169103 -0.504941  0.300581   0.734880  ...   0.487674  -0.039227  -0.004200   
169104  0.000000  0.000000   0.000000  ...   1.375148   0.573437   0.048963   
169105 -0.084528 -0.282901  -0.130856  ...  -0.385030   0.208333  -0.662432   

        change_42  change_43  change_44  change_45  change_46  customer_id  \
0        0.505719   0.077567  -0.104260  -0.427164  -0.678917       100000   
1        0.113218   0.094321   0.133010  -0.027273  -0.185933       100001   
2        0.032435  -0.029261  -0.410399  -0.686088  -0.486188       100003   
3       -0.224281  -0.254653   0.076006  -0.345927  -0.871418       100004   
4        0.133936   0.095264  -0.040343  -0.082951  -0.136606       100005   
...           ...        ...        ...        ...        ...          ...   
169101   0.056036  -0.000394   0.048160  -0.105187  -0.204376       399986   
169102   0.194591  -0.097115  -0.449524  -0.690370  -0.964566       399987   
169103  -0.061192   0.053291  -0.115601  -0.623511  -0.206032       399991   
169104  -0.186639  -0.152110  -0.428181  -0.445366  -0.510708       399994   
169105  -0.510753  -1.000000   0.000000   0.000000   0.000000       399999   

        churn_next_month  
0                      0  
1                      0  
2                      1  
3                      1  
4                      0  
...                  ...  
169101                 0  
169102                 1  
169103                 0  
169104                 1  
169105                 0  

[169106 rows x 48 columns]

#### Evaluación y entrenamiento del modelo

In [54]:
def train_and_evaluate_model(df, n):
    """
    Train an XGBoost model using the given DataFrame and evaluate its performance.
    Additionally, iterate over the first n rows to display predictions and actual values.

    Args:
    df (DataFrame): The input data containing features and labels.
    n (int): Number of rows to iterate over for displaying predictions.

    Returns:
    model: The trained XGBoost model.
    """
    # Separate features and labels
    X = df.drop(['customer_id', 'churn_next_month'], axis=1)
    y = df['churn_next_month']

    # Apply SMOTE to balance the classes
    X_resampled, y_resampled = SMOTE().fit_resample(X, y)

    # Split the data into training and testing sets
    X_train, X_test, y_train, y_test = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42)

    # Train the model
    model = XGBClassifier(use_label_encoder=False, eval_metric='auc')
    model.fit(X_train, y_train)

    # Predict probabilities on the test set
    y_pred_prob = model.predict_proba(X_test)[:, 1]

    # Calculate evaluation metrics
    precision, recall, thresholds = precision_recall_curve(y_test, y_pred_prob)

    y_pred = model.predict(X_test)

    accuracy = accuracy_score(y_test, y_pred)
    f1 = f1_score(y_test, y_pred)
    precision = precision_score(y_test, y_pred)
    recall = recall_score(y_test, y_pred)
    roc_auc = roc_auc_score(y_test, y_pred_prob)
    conf_matrix = confusion_matrix(y_test, y_pred)
    class_report = classification_report(y_test, y_pred)

    # Print evaluation metrics
    print(f"Accuracy: {accuracy}")
    print(f"F1 Score: {f1}")
    print(f"Precision: {precision}")
    print(f"Recall: {recall}")
    print(f"ROC AUC: {roc_auc}")
    print(f"Confusion Matrix:\n{conf_matrix}")
    print(f"Classification Report:\n{class_report}")

    def loop_first_n_rows(n):
        """
        Iterate over the first n rows and display predictions and actual values.

        Args:
        n (int): Number of rows to iterate over.
        """
        first_n_rows = df.head(n)
        X_first_n = first_n_rows.drop(columns=['customer_id', 'churn_next_month'])
        y_first_n = first_n_rows['churn_next_month']
        y_pred_first_n = model.predict(X_first_n)

        correct_predictions = 0
        for i in range(n):
            print(f"Row {i+1}: Predicted: {y_pred_first_n[i]}, Actual: {y_first_n.iloc[i]}")
            if y_pred_first_n[i] == y_first_n.iloc[i]:
                correct_predictions += 1

        accuracy_first_n = correct_predictions / n
        print(f"Accuracy for the first {n} predictions: {accuracy_first_n}")

    # Call the function with the given value of n
    loop_first_n_rows(n)

    return model

# Example usage
df = resultados_df
n = len(df)  # n is the length of the dataset
model = train_and_evaluate_model(df, n)



Accuracy: 0.9247403946002077
F1 Score: 0.9274143068178974
Precision: 0.9020066238067407
Recall: 0.9542948420672953
ROC AUC: 0.9731461470975754
Confusion Matrix:
[[17101  2012]
 [  887 18520]]
Classification Report:
              precision    recall  f1-score   support

           0       0.95      0.89      0.92     19113
           1       0.90      0.95      0.93     19407

    accuracy                           0.92     38520
   macro avg       0.93      0.92      0.92     38520
weighted avg       0.93      0.92      0.92     38520

Row 1: Predicted: 0, Actual: 0
Row 2: Predicted: 0, Actual: 0
Row 3: Predicted: 1, Actual: 1
Row 4: Predicted: 1, Actual: 1
Row 5: Predicted: 0, Actual: 0
Row 6: Predicted: 0, Actual: 0
Row 7: Predicted: 1, Actual: 1
Row 8: Predicted: 0, Actual: 0
Row 9: Predicted: 1, Actual: 0
Row 10: Predicted: 0, Actual: 0
Row 11: Predicted: 0, Actual: 0
Row 12: Predicted: 0, Actual: 0
Row 13: Predicted: 1, Actual: 1
Row 14: Predicted: 0, Actual: 0
Row 15: Predicted: 

#### Preprocesamiento de datos de predicción

In [55]:
def preprocess_prediction_data(file_path, target_month):
    """
    Preprocess the prediction data from the given CSV file for a specified target month.

    Args:
    file_path (str): Path to the CSV file containing the sales data.
    target_month (str): The target month for prediction in 'YYYY-MM-DD' format.

    Returns:
    df_pred_sin (DataFrame): Processed DataFrame without the initial customer_id columns.
    result_df_pred (DataFrame): Fully processed DataFrame with all columns.
    """
    # Read the CSV file
    df_pred = pd.read_csv(file_path)
    
    # Convert the 'month' column to date format
    df_pred['month'] = pd.to_datetime(df_pred['month'].astype(str), format='%Y%m')

    # Sort dates within each 'customer_id' group
    df_pred = df_pred.sort_values(by=['customer_id', 'month'])
    
    # Filter customer_ids with transactions in the target month
    month_customers = df_pred[df_pred['month'] == target_month]['customer_id']
    
    # Filter the DataFrame to keep only rows with customer_ids in month_customers
    df_filtered_pred = df_pred[df_pred['customer_id'].isin(month_customers)]
    
    # Group by 'customer_id' and create lists of 'amount'
    df_grouped_pred = df_filtered_pred.groupby('customer_id')['amount'].apply(list).reset_index()
    
    # Determine the maximum length of 'amount' lists
    max_length_pred = df_grouped_pred['amount'].apply(len).max()

    # Pad the lists at the beginning to have the same length
    df_grouped_pred['amount'] = df_grouped_pred['amount'].apply(lambda x: [0] * (max_length_pred - len(x)) + x)

    # Separate the 'amount' column into multiple columns
    amount_df_pred = pd.DataFrame(df_grouped_pred['amount'].to_list(), columns=[f'amount_{i+1}' for i in range(max_length_pred)])

    # Join the resulting DataFrames
    result_df_pred = pd.concat([df_grouped_pred.drop(columns=['amount']), amount_df_pred], axis=1)
    
    # Remove the first two columns from the resulting DataFrame
    df_pred_sin = result_df_pred.drop(result_df_pred.columns[:2], axis=1)
    
    return df_pred_sin, result_df_pred

# Example usage
file_path = "sales.csv"
target_month = '2023-11-01'
df_pred_sin, result_df_pred = preprocess_prediction_data(file_path, target_month)

#### Visualización de datos predictivos ya preprocesados

In [56]:
# Visualizing df_pred_sin dataset
df_pred_sin

amount_2  amount_3  amount_4  amount_5   amount_6   amount_7  \
0       45.1530   28.5473   51.2210   70.6396    66.4318    59.0138   
1      128.5816  112.9212  116.7928  122.2274   117.4014   121.4014   
2        0.0000    0.0000    0.0000    0.0000     0.0000     0.0000   
3      421.3517  457.7764  410.2522  509.0340   947.6391   945.1321   
4      902.6433  717.6330  763.1393  898.9159  1060.4741  1337.8840   
...         ...       ...       ...       ...        ...        ...   
94267  917.8488  737.7711  721.2333  867.9350   880.0906  1002.8847   
94268   33.7443   28.0285   21.2577   22.0559    32.5173    33.2338   
94269    0.0000    0.0000    0.0000    0.0000     0.0000     0.0000   
94270    3.8746    4.4804   15.2166   26.0712    39.0483    25.6564   
94271   96.2371   88.9208   76.5194  113.3400   111.3280   123.0147   

        amount_8   amount_9  amount_10  amount_11  ...  amount_40  \
0        90.7214    64.1777    37.6583    50.0724  ...    46.6362   
1       164.7714   183.1189   189.3811   159.5931  ...    66.5099   
2         0.0000     0.0000    33.4624   117.8933  ...   204.9193   
3       786.3095   768.8456   832.6491   660.6236  ...   737.0385   
4      1029.2719  1152.8582  1042.6199  1019.9172  ...   919.2831   
...          ...        ...        ...        ...  ...        ...   
94267  1402.3391   762.3310   816.7404   875.1308  ...  1397.6234   
94268    42.2725    40.1472    45.3371    40.0493  ...    10.8298   
94269     0.0000     0.0000     0.0000     0.0000  ...   284.6913   
94270    22.2324    16.0075     2.9235    21.6978  ...    26.4990   
94271   105.8403    97.3848    88.6620    44.7519  ...     0.0000   

         amount_41    amount_42    amount_43    amount_44    amount_45  \
0        47.563753    18.175400    25.572400    40.299500    30.681900   
1        84.713800    50.651800    51.800100    62.251200    62.557500   
2       306.376800   231.761000   259.851900   297.605900   312.957300   
3      1029.060861  1155.641657  1224.266975  1272.383818  1464.956339   
4       869.166045  1014.948400  1007.815302  1177.766000  1405.123197   
...            ...          ...          ...          ...          ...   
94267  1523.146700  1023.598387  1405.355500  1882.919900   933.467500   
94268    14.493000    12.248300    12.459600     9.859700     5.854200   
94269   258.322400   479.959300   580.589900   539.388298   580.148800   
94270    28.462800    24.343000    28.241000    21.125300    30.871800   
94271    32.124000     6.692500     6.410700     0.000000     0.000000   

         amount_46    amount_47    amount_48    amount_49  
0        32.899000     3.522400     8.171900    35.259100  
1        78.852000    58.700800    53.276400    43.240800  
2       272.974100   264.353893   199.571800   152.262700  
3      1464.483096  1299.169500  1110.038474   992.067200  
4      1434.088245  1350.894000   982.924200  1126.959138  
...            ...          ...          ...          ...  
94267  1220.680237  1025.860993  1293.301613   873.917300  
94268     7.502600     6.939100     5.635800     8.902000  
94269   593.305550   456.716700   378.706500   506.855043  
94270    15.114400     2.198900    11.547300    20.993900  
94271     0.000000     0.000000     0.000000     9.862600  

[94272 rows x 48 columns]

#### Obteninedo los datos a predecir

In [66]:
df_sales = pd.read_csv("sales.csv")
# Filtering rows where "churn_next_month" has a null value.
df_filtered = df_sales[df_sales["churn_next_month"].isna()]
df_filtered

customer_id   month       amount  churn_next_month
48            100000  202311    35.259100               NaN
97            100001  202311    43.240800               NaN
187           100005  202311   152.262700               NaN
236           100006  202311   992.067200               NaN
320           100008  202311  1126.959138               NaN
...              ...     ...          ...               ...
5385927       399981  202311   873.917300               NaN
5385976       399982  202311     8.902000               NaN
5386019       399986  202311   506.855043               NaN
5386116       399991  202311    20.993900               NaN
5386174       399999  202311     9.862600               NaN

[94272 rows x 4 columns]

#### Obteniendo predicciones

In [78]:
def porcentaje_cambio(suma_anterior, suma_actual):
    """
    Calculate the percentage change between two sums, handling division by zero.

    Args:
    suma_anterior (float): The previous sum.
    suma_actual (float): The current sum.

    Returns:
    float: The percentage change.
    """
    if suma_anterior == 0:
        if suma_actual > 0:
            return np.inf
        elif suma_actual < 0:
            return -np.inf
        else:
            return 0
    return (suma_actual - suma_anterior) / suma_anterior * 100

def preddicciones_df(df_pred_sin):
    """
    Calculate percentage changes for each row in the prediction DataFrame and predict churn.

    Args:
    df_pred_sin (DataFrame): Processed DataFrame without initial customer_id columns.

    Returns:
    DataFrame: DataFrame containing customer IDs and churn predictions.
    """
    resultados_pred = []

    # Iterate over each row in the DataFrame
    for _, row in df_pred_sin.iterrows():
        array = row.values
        cambios = []

        # Iterate over overlapping windows of 1 element
        for i in range(len(array) - 2):
            suma_anterior = array[i] + array[i + 1]
            suma_actual = array[i + 1] + array[i + 2]
            cambio = porcentaje_cambio(suma_anterior, suma_actual)
            cambios.append(cambio)

        resultados_pred.append(cambios)

    # Convert the list of results into a new DataFrame
    resultados_df_pred = pd.DataFrame(resultados_pred, columns=[f'change_{i+1}' for i in range(len(resultados_pred[0]))])

    # Replace NaN with 0
    resultados_df_pred.fillna(0, inplace=True)

    # Replace inf with 1
    resultados_df_pred.replace([np.inf, -np.inf], 1, inplace=True)

    # Predict churn using the model on the processed prediction data
    y_pred_prob_nuevo_a = model.predict(resultados_df_pred)

    # Create a DataFrame with the customer IDs
    final_a = result_df_pred['customer_id']
    df_final_a = pd.DataFrame(final_a)

    # Merge df_final_a with df_filtered on 'customer_id' to include the 'month' column
    df_final_a = df_final_a.merge(df_filtered[['customer_id', 'month']], on='customer_id', how='left')
    # Add the prediction results to the DataFrame
    df_final_a['Prediction'] = y_pred_prob_nuevo_a

    return df_final_a

# Example usage
df_final_a = preddicciones_df(df_pred_sin)
# Saving to csv file the predictions
df_final_a.to_csv('predictions.csv', index=False)
print("Predictions saved to predictions.csv")


Predictions saved to predictions.csv


#### Visualizando dataset con predicciones.

In [79]:
# Visualizing predictions
df_final_a

customer_id   month  Prediction
0           100000  202311           0
1           100001  202311           0
2           100005  202311           0
3           100006  202311           0
4           100008  202311           0
...            ...     ...         ...
94267       399981  202311           0
94268       399982  202311           0
94269       399986  202311           1
94270       399991  202311           0
94271       399999  202311           0

[94272 rows x 3 columns]

#### Contando número de clientes predecidos como churn

In [80]:
# Counting number of clients predicted as churn_next_month
df_1 = df_final_a[df_final_a['Prediction'] == 1]
df_1

customer_id   month  Prediction
6           100011  202311           1
11          100032  202311           1
14          100039  202311           1
30          100083  202311           1
44          100131  202311           1
...            ...     ...         ...
94231       399878  202311           1
94232       399884  202311           1
94247       399928  202311           1
94253       399947  202311           1
94269       399986  202311           1

[18821 rows x 3 columns]